# Objective:

In this notebook, you will see demo of how [Redshift supports Iceberg tables](https://aws.amazon.com/about-aws/whats-new/2023/11/amazon-redshift-support-apache-iceberg/).

# Pre-requisites

1. Create Redshift Serverelss workgroup and namespace.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-console-workgroups-create-workgroup-wizard.html) to create the wokrgroup and namespace.
2. Ensure you setup an IAM role as default IAM role.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/default-iam-role.html#managing-iam-role-console) for instructions.

## Setup Test Data

We will need to create the database and Iceberg table in Athena

--create the database

create database icebergdb;

--create the table

create table icebergdb.myicebergtable (
  id int  ,
  name string 
 )
LOCATION 's3://<YOUR-BUCKET>/icebergdb' 
TBLPROPERTIES (
  'table_type'='ICEBERG',
  'format'='parquet',
  'write_compression'='snappy',
  'optimize_rewrite_delete_file_threshold'='10'
);

--insert some data

insert into icebergdb.myicebergtable values 
(1, 'Mary'),
(2, 'Anne'),
(3, 'John'),
(4, 'Robert');

--validate the data inserted

select * from icebergdb.myicebergtable;


Please refer this [link](https://docs.aws.amazon.com/athena/latest/ug/getting-started.html) to get more details on Athena.

Please refer this [link](https://aws.amazon.com/pm/serv-s3/?gclid=EAIaIQobChMIio7Ri9LRgwMV2mlHAR2_6g9jEAAYASAAEgJDiPD_BwE&trk=fecf68c9-3874-4ae2-a7ed-72b6d19c8034&sc_channel=ps&ef_id=EAIaIQobChMIio7Ri9LRgwMV2mlHAR2_6g9jEAAYASAAEgJDiPD_BwE:G:s&s_kwcid=AL!4422!3!536452728638!e!!g!!aws%20s3!11204620052!112938567994) to get more details on S3

## Create the external schema

In [0]:
create external schema icebergdb
from data catalog
database 'icebergdb'
iam_role default;

## Access the data from the iceberg table

You should see the same data as in Athena

In [0]:
select * from icebergdb.myicebergtable;

## Adding more data

You will be able to see any changes on the iceberg data. As an example, let's change the data

insert into icebergdb.myicebergtable values 
(5, 'Beth'),
(6, 'James');

delete from icebergdb.myicebergtable where id in (1,3);

update icebergdb.myicebergtable set name='Dave' where id=4;

--you should confirm that all changes were made on Athena

select * from icebergdb.myicebergtable;

## Confirm the data on Redshift

Query the data one more time on Amazon Redshift and you will see the changes

In [0]:
select * from icebergdb.myicebergtable;

## Join with Redshift tables

Amazon Redshift allows us to join tables from different sourcers. Let's create a table on Redshift and add some data.

In [0]:
--create the schema
create schema redshiftdb;

--create the table
create table redshiftdb.myredshifttable
(id int,
role char(10));

--ingest some data
insert into redshiftdb.myredshifttable values 
(1,'Teacher'),
(2, 'Engineer'),
(3, 'Doctor'),
(4, 'IT');

--validate the data
select * from redshiftdb.myredshifttable;

## Join data from iceberg and Redshift

Now , let's create a view joining between the iceberg table and Redshift local table

In [0]:
create or replace view redshiftdb.myjoin as 
select i.id, i.name,r.role 
from icebergdb.myicebergtable i,
redshiftdb.myredshifttable r
where i.id=r.id
WITH NO SCHEMA BINDING;

select * from redshiftdb.myjoin;
select * from redshiftdb.myjoin where id = 2;

## Considerations and Limitations

Please refer to this [link](https://docs.aws.amazon.com/redshift/latest/dg/querying-iceberg.html) to understand the considerations and limitations.

## Cleanup

1. Delete Redshift Serverless workgroup. Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless_delete-workgroup.html) for documentation to delete workgroup.

2. Delete Redshift Serverelss associated namespace. Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-console-namespace-delete.html) for documentation to delete workgroup.

3. Drop the database and table on Athena: drop database icebergdb cascade;